### konlpy를 사용한 형태소분리와 Word2Vec를 사용한 벡터변환

In [214]:
# # 한국어 전처리를 위한
!pip install konlpy
# !pip install Twitter
# !pip install tqdm
!pip install gensim
# !pip install --upgrade jupyter ipywidgets

Defaulting to user installation because normal site-packages is not writeable
Defaulting to user installation because normal site-packages is not writeable


In [215]:
import os # 운영 체제 관련 작업을 수행하기 위한 Python 표준 라이브러리 중 하나 -> 자바 환경 변수를 설정하기 위해 사용
import pandas as pd # 데이터 조작 및 분석을 위한 파이썬 라이브러리 -> 데이터를 데이터프레임으로 로드하고 조작하는 데 사용
import numpy as np # 배열 및 수치 연산을 수행하기 위한 라이브러리 -> 다차원 배열 및 수학적 함수를 다루는 데 사용
from konlpy.tag import Okt # Konlpy 라이브러리에서 제공하는 한국어 형태소 분석기 중 하나 ->  Okt를 초기화하는 데 사용
from gensim.models.word2vec import Word2Vec # Gensim 라이브러리에서 제공하는 Word2Vec 모델을 생성하기 위한 클래스 -> 단어를 고차원 벡터로 표현하여 단어 간 유사성 및 의미 관계를 파악

In [216]:
# 본인 컴퓨터와 자바 설치 경로 설정
os.environ["JAVA_HOME"] = "C:\Program Files\Java\jdk-11"

In [217]:
# 데이터를 데이터프레임으로 로드
book_data = pd.read_csv('../cleaned_data.csv', encoding='utf-8')# 데이터 파일 경로
book_data

SEQ_NO  ISBN_THIRTEEN_NO VLM_NM                              TITLE_NM  \
0     6352228     9791156759270    NaN   너에게 목소리를 보낼게  달빛천사 성우 이용신의 첫 번째 에세이   
1     6352229     9791168120877    NaN  일기에도 거짓말을 쓰는 사람  99년생 시인의 자의식 과잉 에세이   
2     6352230     9791168120839    NaN            본격 한중일 세계사 12  임오군란과 통킹 위기   
3     6352231     9791168120846    NaN   즉시 기분을 바꿔드립니다  신기하게 마음이 편해지는 응급 처방전   
4     6352232     9791168120747    NaN               오늘도 리추얼  음악 나에게 선물하는 시간   
...       ...               ...    ...                                   ...   
1997  6354246     9791164670871    NaN                          학교 서클대화가 필요해   
1998  6354247     9788994229003    NaN                      People Make City   
1999  6354248     9788994027203    NaN                                 동방해경표   
2000  6354249     9791156759126    NaN                      큰글자도서 그렇다면 정상입니다   
2001  6354250     9788988963258    NaN                                 그 사람들   

                  AUTHR_NM PUBLISHER_NM PBLICTE_DE  ADTION_SMBL_NM  PRC_VALUE  \
0                  이용신 지은이          푸른숲        NaN             NaN   160000.0   
1                  차도하 지은이       위즈덤하우스        NaN             NaN   158000.0   
2                굽시니스트 지은이       위즈덤하우스        NaN             NaN   148000.0   
3     올리비아 레메스 지은이 김잔디 옮긴이       위즈덤하우스        NaN             NaN   140000.0   
4                  정혜윤 지은이       위즈덤하우스        NaN             NaN   150000.0   
...                    ...          ...        ...             ...        ...   
1997       손연일 심선화 장경아 지은이          북트리        NaN             NaN   160000.0   
1998               이상환 지은이       디자인로커스        NaN             NaN   150000.0   
1999                 김려 지음        미디어버스        NaN             NaN        NaN   
2000               하지현 지은이          푸른숲        NaN             NaN   360000.0   
2001                김규태 지음           말쌈        NaN             NaN        NaN   

                                              IMAGE_URL  \
0     httpsimagealadincokrproduct284158coverk6528351...   
1     httpsimagealadincokrproduct2841466coverk202835...   
2     httpsimagealadincokrproduct2841447coverk402835...   
3     httpsimagealadincokrproduct2841430coverk892835...   
4     httpsimagealadincokrproduct2841380coverk202835...   
...                                                 ...   
1997  httpsimagealadincokrproduct2837599coverk262835...   
1998  httpsimagealadincokrproduct141865cover89942290...   
1999                                                NaN   
2000  httpsimagealadincokrproduct2834689coverk292835...   
2001                                                NaN   

                                         BOOK_INTRCN_CN  KDC_NM  \
0     2004년 방영한 애니메이션 달빛천사에서 주인공 루나풀문 역을 맡으며 90년대생들에...     NaN   
1     그러니 나는 말하고 싶은 것을 말하겠다침착하게 사랑하기 차도하 시인 첫 에세이새롭고...     NaN   
2     한중일 관계의 결정적 분기점인 임오군란의 막전 막후를 다룬다 러시아의 세력 확장을 ...     NaN   
3     누구에게나 기분 구급상자가 필요하다 하나씩 하나씩 차근차근 좋은 기분을 쌓고 건강한...     NaN   
4     나다운 일상을 만드는 사람들의 이야기를 담은 오늘도 리추얼 시리즈가 위즈덤하우스에서...     NaN   
...                                                 ...     ...   
1997  평화로운 학교 공동체의 여정으로 가는 친절한 안내서 관계를 회복하고 배움이 일어나는...     NaN   
1998  따뜻한 성북동 만들기피블메이크시티시리즈는 대상지역의 문화 예술적 개발 방법론을 연구...     NaN   
1999                                                NaN     NaN   
2000  심야 치유 식당 사랑하기에 결코 늦지 않았다 엄마의 빈틈이 아이를 키운다 등을 통해...     NaN   
2001                                                NaN     NaN   

       TITLE_SBST_NM AUTHR_SBST_NM  TWO_PBLICTE_DE INTNT_BOOKST_BOOK_EXST_AT  \
0                NaN           NaN      20211203.0                       NaN   
1                NaN           NaN      20211206.0                       NaN   
2                NaN           NaN      20211201.0                       NaN   
3                NaN           NaN      20211201.0                       NaN   
4                NaN           NaN      20211201.0                       NaN   
...              ...           ...             ...                       ...   

### 텍스트 전처리

In [218]:
# 형태소 분리를 위한 Konlpy 객체 초기화
twitter = Okt()

In [219]:
#텍스트를 전처리 하는 함수
#BOOK_INTRCN_CN: 전처리할 도서 줄거리
def preprocessingText(BOOK_INTRCN_CN):
    #전처리한 결과를 저장 할 리스트
    stems = []
    #text 를 단어로 나누고 품사를 붙여서 리턴
    #stem=True : 단어의 기본형으로 변환  ex) 같습니다,같았습니다 -> 같다.  
    tagged_review = twitter.pos(BOOK_INTRCN_CN,stem=True)

    #tagged에서 하나를 꺼내서 word,pos에 대입
    #단어는 word, 품사는 pos에 대입
    for word,pos in tagged_review:
        #len(word) : 단어의 글자수가 2글자 이상이면
        #품사가 Noun(명사) 또는 Adjective(형용사) 일경우에만 word(단어) 를 stems에 추가
        if pos=="Noun" or pos=='Adjective':
            stems.append(word)

    #리스트인 stems를 문자열로 만들어서 ( "".join(stems) ) 리턴       
    return " ".join(stems)

In [220]:
preprocessingText(book_data['BOOK_INTRCN_CN'][0])

'방영 애니메이션 달빛천사 주인공 루나 풀문 역 보석 같다 추억 선물 성우 이용신 첫 에세이 수많다 작품 주연 쉬 대중 행복 전 성우 이용신 발자취 확인 수 있다'

In [221]:
# 데이터프레임의 'BOOK_INTRCN_CN' 열에 NaN 값이 있을 때 빈 문자열로 대체 및 전처리
book_data['BOOK_INTRCN_CN_clear'] = book_data['BOOK_INTRCN_CN'].fillna('').apply(preprocessingText)

In [222]:
# Word2Vec 모델 훈련을 위한 데이터 준비
sentences = book_data['BOOK_INTRCN_CN'].tolist()

In [223]:
# 데이터프레임의 'BOOK_INTRCN_CN' 열에 NaN 값이 있을 때 빈 문자열로 대체
tokenized_data = book_data['BOOK_INTRCN_CN'].apply(lambda x: preprocessingText(str(x))).fillna('')

In [224]:
book_data

SEQ_NO  ISBN_THIRTEEN_NO VLM_NM                              TITLE_NM  \
0     6352228     9791156759270    NaN   너에게 목소리를 보낼게  달빛천사 성우 이용신의 첫 번째 에세이   
1     6352229     9791168120877    NaN  일기에도 거짓말을 쓰는 사람  99년생 시인의 자의식 과잉 에세이   
2     6352230     9791168120839    NaN            본격 한중일 세계사 12  임오군란과 통킹 위기   
3     6352231     9791168120846    NaN   즉시 기분을 바꿔드립니다  신기하게 마음이 편해지는 응급 처방전   
4     6352232     9791168120747    NaN               오늘도 리추얼  음악 나에게 선물하는 시간   
...       ...               ...    ...                                   ...   
1997  6354246     9791164670871    NaN                          학교 서클대화가 필요해   
1998  6354247     9788994229003    NaN                      People Make City   
1999  6354248     9788994027203    NaN                                 동방해경표   
2000  6354249     9791156759126    NaN                      큰글자도서 그렇다면 정상입니다   
2001  6354250     9788988963258    NaN                                 그 사람들   

                  AUTHR_NM PUBLISHER_NM PBLICTE_DE  ADTION_SMBL_NM  PRC_VALUE  \
0                  이용신 지은이          푸른숲        NaN             NaN   160000.0   
1                  차도하 지은이       위즈덤하우스        NaN             NaN   158000.0   
2                굽시니스트 지은이       위즈덤하우스        NaN             NaN   148000.0   
3     올리비아 레메스 지은이 김잔디 옮긴이       위즈덤하우스        NaN             NaN   140000.0   
4                  정혜윤 지은이       위즈덤하우스        NaN             NaN   150000.0   
...                    ...          ...        ...             ...        ...   
1997       손연일 심선화 장경아 지은이          북트리        NaN             NaN   160000.0   
1998               이상환 지은이       디자인로커스        NaN             NaN   150000.0   
1999                 김려 지음        미디어버스        NaN             NaN        NaN   
2000               하지현 지은이          푸른숲        NaN             NaN   360000.0   
2001                김규태 지음           말쌈        NaN             NaN        NaN   

                                              IMAGE_URL  \
0     httpsimagealadincokrproduct284158coverk6528351...   
1     httpsimagealadincokrproduct2841466coverk202835...   
2     httpsimagealadincokrproduct2841447coverk402835...   
3     httpsimagealadincokrproduct2841430coverk892835...   
4     httpsimagealadincokrproduct2841380coverk202835...   
...                                                 ...   
1997  httpsimagealadincokrproduct2837599coverk262835...   
1998  httpsimagealadincokrproduct141865cover89942290...   
1999                                                NaN   
2000  httpsimagealadincokrproduct2834689coverk292835...   
2001                                                NaN   

                                         BOOK_INTRCN_CN  KDC_NM  \
0     2004년 방영한 애니메이션 달빛천사에서 주인공 루나풀문 역을 맡으며 90년대생들에...     NaN   
1     그러니 나는 말하고 싶은 것을 말하겠다침착하게 사랑하기 차도하 시인 첫 에세이새롭고...     NaN   
2     한중일 관계의 결정적 분기점인 임오군란의 막전 막후를 다룬다 러시아의 세력 확장을 ...     NaN   
3     누구에게나 기분 구급상자가 필요하다 하나씩 하나씩 차근차근 좋은 기분을 쌓고 건강한...     NaN   
4     나다운 일상을 만드는 사람들의 이야기를 담은 오늘도 리추얼 시리즈가 위즈덤하우스에서...     NaN   
...                                                 ...     ...   
1997  평화로운 학교 공동체의 여정으로 가는 친절한 안내서 관계를 회복하고 배움이 일어나는...     NaN   
1998  따뜻한 성북동 만들기피블메이크시티시리즈는 대상지역의 문화 예술적 개발 방법론을 연구...     NaN   
1999                                                NaN     NaN   
2000  심야 치유 식당 사랑하기에 결코 늦지 않았다 엄마의 빈틈이 아이를 키운다 등을 통해...     NaN   
2001                                                NaN     NaN   

       TITLE_SBST_NM AUTHR_SBST_NM  TWO_PBLICTE_DE INTNT_BOOKST_BOOK_EXST_AT  \
0                NaN           NaN      20211203.0                       NaN   
1                NaN           NaN      20211206.0                       NaN   
2                NaN           NaN      20211201.0                       NaN   
3                NaN           NaN      20211201.0                       NaN   
4                NaN           NaN      20211201.0                       NaN   
...              ...           ...             ...                       ...   

In [225]:
#BOOK_INTRCN_CN_clear의 마지막에 " " 추가
book_data["BOOK_INTRCN_CN_clear"] = book_data['BOOK_INTRCN_CN_clear'].astype(str) + " "

In [226]:
#data.split(" ") : 문자열을 공백기준으로 잘라서 리스트로 변환
book_data["BOOK_INTRCN_CN_clear"].apply(lambda data : data.split(" "))

0       [방영, 애니메이션, 달빛천사, 주인공, 루나, 풀문, 역, 보석, 같다, 추억, ...
1       [그렇다, 나, 말, 것, 말, 침착하다, 사랑, 차도, 시인, 첫, 에세이, 새,...
2       [한중일, 관계, 결정, 분기점, 임오군란, 막후, 러시아, 세력, 확장, 경계, ...
3       [누구, 기분, 구급상자, 필요하다, 하나, 하나, 차근차근, 좋다, 기분, 건강하...
4       [일상, 사람, 이야기, 오늘, 리추얼, 시리즈, 위즈, 덤, 하우스, 간, 오늘,...
                              ...                        
1997    [평화롭다, 학교, 공동체, 여정, 친절하다, 안내서, 관계, 회복하다, 배움, 평...
1998    [따뜻하다, 성북동, 만들기, 피블, 메이크, 시티, 시리즈, 대상, 지역, 문화,...
1999                                                 [, ]
2000    [심야, 치유, 식당, 사랑, 결코, 엄마, 빈틈, 아이, 등, 통해, 사람, 문제...
2001                                                 [, ]
Name: BOOK_INTRCN_CN_clear, Length: 2002, dtype: object

In [227]:
#df["BOOK_INTRCN_CN_clear"].apply(lambda data : data.split(" ")) : BOOK_INTRCN_CN_clear 컬럼을 공백을 기준으로 단어별로 분리해서 리턴
book_data["tokenized_data"] = book_data["BOOK_INTRCN_CN_clear"].apply(lambda data : data.split(" "))

In [228]:
book_data

SEQ_NO  ISBN_THIRTEEN_NO VLM_NM                              TITLE_NM  \
0     6352228     9791156759270    NaN   너에게 목소리를 보낼게  달빛천사 성우 이용신의 첫 번째 에세이   
1     6352229     9791168120877    NaN  일기에도 거짓말을 쓰는 사람  99년생 시인의 자의식 과잉 에세이   
2     6352230     9791168120839    NaN            본격 한중일 세계사 12  임오군란과 통킹 위기   
3     6352231     9791168120846    NaN   즉시 기분을 바꿔드립니다  신기하게 마음이 편해지는 응급 처방전   
4     6352232     9791168120747    NaN               오늘도 리추얼  음악 나에게 선물하는 시간   
...       ...               ...    ...                                   ...   
1997  6354246     9791164670871    NaN                          학교 서클대화가 필요해   
1998  6354247     9788994229003    NaN                      People Make City   
1999  6354248     9788994027203    NaN                                 동방해경표   
2000  6354249     9791156759126    NaN                      큰글자도서 그렇다면 정상입니다   
2001  6354250     9788988963258    NaN                                 그 사람들   

                  AUTHR_NM PUBLISHER_NM PBLICTE_DE  ADTION_SMBL_NM  PRC_VALUE  \
0                  이용신 지은이          푸른숲        NaN             NaN   160000.0   
1                  차도하 지은이       위즈덤하우스        NaN             NaN   158000.0   
2                굽시니스트 지은이       위즈덤하우스        NaN             NaN   148000.0   
3     올리비아 레메스 지은이 김잔디 옮긴이       위즈덤하우스        NaN             NaN   140000.0   
4                  정혜윤 지은이       위즈덤하우스        NaN             NaN   150000.0   
...                    ...          ...        ...             ...        ...   
1997       손연일 심선화 장경아 지은이          북트리        NaN             NaN   160000.0   
1998               이상환 지은이       디자인로커스        NaN             NaN   150000.0   
1999                 김려 지음        미디어버스        NaN             NaN        NaN   
2000               하지현 지은이          푸른숲        NaN             NaN   360000.0   
2001                김규태 지음           말쌈        NaN             NaN        NaN   

                                              IMAGE_URL  \
0     httpsimagealadincokrproduct284158coverk6528351...   
1     httpsimagealadincokrproduct2841466coverk202835...   
2     httpsimagealadincokrproduct2841447coverk402835...   
3     httpsimagealadincokrproduct2841430coverk892835...   
4     httpsimagealadincokrproduct2841380coverk202835...   
...                                                 ...   
1997  httpsimagealadincokrproduct2837599coverk262835...   
1998  httpsimagealadincokrproduct141865cover89942290...   
1999                                                NaN   
2000  httpsimagealadincokrproduct2834689coverk292835...   
2001                                                NaN   

                                         BOOK_INTRCN_CN  KDC_NM  \
0     2004년 방영한 애니메이션 달빛천사에서 주인공 루나풀문 역을 맡으며 90년대생들에...     NaN   
1     그러니 나는 말하고 싶은 것을 말하겠다침착하게 사랑하기 차도하 시인 첫 에세이새롭고...     NaN   
2     한중일 관계의 결정적 분기점인 임오군란의 막전 막후를 다룬다 러시아의 세력 확장을 ...     NaN   
3     누구에게나 기분 구급상자가 필요하다 하나씩 하나씩 차근차근 좋은 기분을 쌓고 건강한...     NaN   
4     나다운 일상을 만드는 사람들의 이야기를 담은 오늘도 리추얼 시리즈가 위즈덤하우스에서...     NaN   
...                                                 ...     ...   
1997  평화로운 학교 공동체의 여정으로 가는 친절한 안내서 관계를 회복하고 배움이 일어나는...     NaN   
1998  따뜻한 성북동 만들기피블메이크시티시리즈는 대상지역의 문화 예술적 개발 방법론을 연구...     NaN   
1999                                                NaN     NaN   
2000  심야 치유 식당 사랑하기에 결코 늦지 않았다 엄마의 빈틈이 아이를 키운다 등을 통해...     NaN   
2001                                                NaN     NaN   

       TITLE_SBST_NM AUTHR_SBST_NM  TWO_PBLICTE_DE INTNT_BOOKST_BOOK_EXST_AT  \
0                NaN           NaN      20211203.0                       NaN   
1                NaN           NaN      20211206.0                       NaN   
2                NaN           NaN      20211201.0                       NaN   
3                NaN           NaN      20211201.0                       NaN   
4                NaN           NaN      20211201.0                       NaN   
...              ...           ...             ...                       ...   

In [229]:
book_data["tokenized_data"]

0       [방영, 애니메이션, 달빛천사, 주인공, 루나, 풀문, 역, 보석, 같다, 추억, ...
1       [그렇다, 나, 말, 것, 말, 침착하다, 사랑, 차도, 시인, 첫, 에세이, 새,...
2       [한중일, 관계, 결정, 분기점, 임오군란, 막후, 러시아, 세력, 확장, 경계, ...
3       [누구, 기분, 구급상자, 필요하다, 하나, 하나, 차근차근, 좋다, 기분, 건강하...
4       [일상, 사람, 이야기, 오늘, 리추얼, 시리즈, 위즈, 덤, 하우스, 간, 오늘,...
                              ...                        
1997    [평화롭다, 학교, 공동체, 여정, 친절하다, 안내서, 관계, 회복하다, 배움, 평...
1998    [따뜻하다, 성북동, 만들기, 피블, 메이크, 시티, 시리즈, 대상, 지역, 문화,...
1999                                                 [, ]
2000    [심야, 치유, 식당, 사랑, 결코, 엄마, 빈틈, 아이, 등, 통해, 사람, 문제...
2001                                                 [, ]
Name: tokenized_data, Length: 2002, dtype: object

### 유사도 측정
- 특정 줄거리와 다른 모든 줄거리 간의 유사도를 측정

In [230]:
from sklearn.metrics.pairwise import cosine_similarity
import random

In [231]:
# 학습용 Word2Vec 모델 훈련(벡터화)
model = Word2Vec(book_data["tokenized_data"], 
                 vector_size=100, #WordVector의 열의 수
                 window=3, # 고려할 앞뒤 폭(앞뒤 3단어)
                 min_count=2, # 사용할 단어의 최소 빈도(2회 이하 단어 무시)
                 sg=1) # 0: CBOW, 1: Skip-gram

In [232]:
#Vector 형태로 변환한 단어 리스트 조회
model.wv.key_to_index

{'': 0,
 '있다': 1,
 '수': 2,
 '문제': 3,
 '학습': 4,
 '개념': 5,
 '구성': 6,
 '수록': 7,
 '책': 8,
 '수학': 9,
 '및': 10,
 '통해': 11,
 '주': 12,
 '것': 13,
 '독해': 14,
 '유형': 15,
 '등': 16,
 '연습': 17,
 '내용': 18,
 '다양하다': 19,
 '기출': 20,
 '주문': 21,
 '이해': 22,
 '이': 23,
 '개': 24,
 '교과': 25,
 '별': 26,
 '공부': 27,
 '단계': 28,
 '단어': 29,
 '과정': 30,
 '교재': 31,
 '속': 32,
 '방법': 33,
 '시험': 34,
 '아이': 35,
 '이야기': 36,
 '제공': 37,
 '위': 38,
 '시리즈': 39,
 '수능': 40,
 '어휘': 41,
 '완성': 42,
 '모의고사': 43,
 '실전': 44,
 '연산': 45,
 '정리': 46,
 '재미있다': 47,
 '생활': 48,
 '핵심': 49,
 '설명': 50,
 '어떻다': 51,
 '기본': 52,
 '작품': 53,
 '지문': 54,
 '계산': 55,
 '대한': 56,
 '학년': 57,
 '영역': 58,
 '적용': 59,
 '대비': 60,
 '만화': 61,
 '권': 62,
 '그': 63,
 '기초': 64,
 '문장': 65,
 '교과서': 66,
 '필수': 67,
 '문학': 68,
 '저자': 69,
 '가지': 70,
 '체계': 71,
 '분석': 72,
 '집': 73,
 '위해': 74,
 '교육': 75,
 '풀이': 76,
 '준비': 77,
 '법': 78,
 '초등': 79,
 '각': 80,
 '가능하다': 81,
 '같다': 82,
 '작가': 83,
 '아니다': 84,
 '자료': 85,
 '해설': 86,
 '글쓰기': 87,
 '사고력': 88,
 '중심': 89,
 '쓰기': 90,
 '집중': 91,
 

In [233]:
#믿음의 인덱스(빈도수 순위 0이 가장 빈도수 높은 단어)
model.wv.key_to_index["믿음"]

1192

In [234]:
#믿음과 비슷한 벡터를 가진 단어 조회
model.wv.most_similar("믿음")

[('중학생', 0.9925969839096069),
 ('계발', 0.9925718307495117),
 ('용어', 0.9924318790435791),
 ('', 0.9924262762069702),
 ('미국', 0.9924148321151733),
 ('의미', 0.9923803806304932),
 ('정리', 0.9923315644264221),
 ('수험생', 0.992322564125061),
 ('심화', 0.992264986038208),
 ('강화', 0.9922565221786499)]

In [235]:
#믿음의 WordVector 조회
model.wv["믿음"]

array([-0.00183343,  0.09976745,  0.0272021 ,  0.0075086 ,  0.01116616,
       -0.08951651, -0.00224324,  0.07525545, -0.07060242,  0.01325758,
       -0.05315768, -0.06027018, -0.07331345,  0.03166179, -0.005809  ,
       -0.015027  ,  0.04430315, -0.00896915,  0.01214357, -0.08510369,
       -0.00912486,  0.08696073, -0.02041449, -0.02359266, -0.03612458,
        0.05743758, -0.04091521, -0.05647093, -0.0339467 ,  0.04927283,
        0.0370685 , -0.02625655, -0.00448393,  0.02816627, -0.00251286,
        0.08102202, -0.03797209,  0.01159236, -0.03747115, -0.05342864,
       -0.01000503, -0.0043155 ,  0.02738062, -0.00293962,  0.06654843,
       -0.05619748,  0.00131602, -0.06738821,  0.00704685, -0.01560336,
        0.01121368, -0.05117438, -0.03350363, -0.02036728, -0.01892473,
        0.02075872,  0.01778271, -0.02470238, -0.03654791, -0.02806306,
        0.01646229,  0.06001706, -0.05447916,  0.01792273, -0.00086944,
        0.01747428,  0.00891044,  0.01707611, -0.09321688,  0.05

In [236]:
#WordVector로 변환한 단어들 word2vec_words 대입
word2vec_words = model.wv.key_to_index.keys()
word2vec_words

dict_keys(['', '있다', '수', '문제', '학습', '개념', '구성', '수록', '책', '수학', '및', '통해', '주', '것', '독해', '유형', '등', '연습', '내용', '다양하다', '기출', '주문', '이해', '이', '개', '교과', '별', '공부', '단계', '단어', '과정', '교재', '속', '방법', '시험', '아이', '이야기', '제공', '위', '시리즈', '수능', '어휘', '완성', '모의고사', '실전', '연산', '정리', '재미있다', '생활', '핵심', '설명', '어떻다', '기본', '작품', '지문', '계산', '대한', '학년', '영역', '적용', '대비', '만화', '권', '그', '기초', '문장', '교과서', '필수', '문학', '저자', '가지', '체계', '분석', '집', '위해', '교육', '풀이', '준비', '법', '초등', '각', '가능하다', '같다', '작가', '아니다', '자료', '해설', '글쓰기', '사고력', '중심', '쓰기', '집중', '확인', '반드시', '한눈', '원리', '도움', '하루', '말', '능력', '강의', '훈련', '중', '최근', '삶', '실제', '사람', '해결', '실력', '난이도', '가능', '서술', '마음', '대상', '자신', '단', '문법', '소설', '향상', '시간', '흥미롭다', '도서', '영어', '부족', '세계', '언어', '동화', '반영', '요청', '효과', '식', '재고', '해외', '반품', '불가하다', '원서', '경우', '우리', '사진', '최신', '제시', '엄선', '취소', '고객', '소개', '대회', '수입', '전기', '북', '독자', '출제', '없다', '학기', '학생', '서로', '간', '갈래', '쪽', '글', '내신', '새롭다', '가장', '동영상', '과목', '스스로', '시

In [237]:
word2vec_words

dict_keys(['', '있다', '수', '문제', '학습', '개념', '구성', '수록', '책', '수학', '및', '통해', '주', '것', '독해', '유형', '등', '연습', '내용', '다양하다', '기출', '주문', '이해', '이', '개', '교과', '별', '공부', '단계', '단어', '과정', '교재', '속', '방법', '시험', '아이', '이야기', '제공', '위', '시리즈', '수능', '어휘', '완성', '모의고사', '실전', '연산', '정리', '재미있다', '생활', '핵심', '설명', '어떻다', '기본', '작품', '지문', '계산', '대한', '학년', '영역', '적용', '대비', '만화', '권', '그', '기초', '문장', '교과서', '필수', '문학', '저자', '가지', '체계', '분석', '집', '위해', '교육', '풀이', '준비', '법', '초등', '각', '가능하다', '같다', '작가', '아니다', '자료', '해설', '글쓰기', '사고력', '중심', '쓰기', '집중', '확인', '반드시', '한눈', '원리', '도움', '하루', '말', '능력', '강의', '훈련', '중', '최근', '삶', '실제', '사람', '해결', '실력', '난이도', '가능', '서술', '마음', '대상', '자신', '단', '문법', '소설', '향상', '시간', '흥미롭다', '도서', '영어', '부족', '세계', '언어', '동화', '반영', '요청', '효과', '식', '재고', '해외', '반품', '불가하다', '원서', '경우', '우리', '사진', '최신', '제시', '엄선', '취소', '고객', '소개', '대회', '수입', '전기', '북', '독자', '출제', '없다', '학기', '학생', '서로', '간', '갈래', '쪽', '글', '내신', '새롭다', '가장', '동영상', '과목', '스스로', '시

In [238]:
for index in range(2):
    # 도서 번호 조회
    NUM = book_data.loc[index,"SEQ_NO"]
    print("NUM=",NUM)
    # 도서 제목 조회
    TITLE = book_data.loc[index,"TITLE_NM"]
    print("TITLE=",TITLE)
    #줄거리 조회
    LINE = book_data.loc[index,"tokenized_data"]
    print("LINE=",LINE)
    doc2vec = None
    count = 0
    for word in LINE: #줄거리에서 단어 1개씩 리턴
        print("word=",word, end="\t")
        if word in word2vec_words: #단어가 WordVector에 포함된 단어 이면
            count += 1 #개수 1증가
            if doc2vec is None: #doc2vect이 None(초기값 맨처음 실행 첫번째 단어) 이면
                doc2vec = model.wv[word] #단어의 WordVector 값 대입
            else: #첫번째 단어 아님
                doc2vec = doc2vec + model.wv[word] #단어의 WordVector 값 추가

    if  doc2vec is not None:
        # 단어 벡터를 모두 더한 벡터의 값을 단어의 개수로 나눠줌
        doc2vec = doc2vec / count
    print()    
    print("="*100)
    print("NUM=",NUM,"TITLE=",TITLE,":doc2vec=",doc2vec)
    print("="*100)

NUM= 6352228
TITLE= 너에게 목소리를 보낼게  달빛천사 성우 이용신의 첫 번째 에세이
LINE= ['방영', '애니메이션', '달빛천사', '주인공', '루나', '풀문', '역', '보석', '같다', '추억', '선물', '성우', '이용신', '첫', '에세이', '수많다', '작품', '주연', '쉬', '대중', '행복', '전', '성우', '이용신', '발자취', '확인', '수', '있다', '']
word= 방영	word= 애니메이션	word= 달빛천사	word= 주인공	word= 루나	word= 풀문	word= 역	word= 보석	word= 같다	word= 추억	word= 선물	word= 성우	word= 이용신	word= 첫	word= 에세이	word= 수많다	word= 작품	word= 주연	word= 쉬	word= 대중	word= 행복	word= 전	word= 성우	word= 이용신	word= 발자취	word= 확인	word= 수	word= 있다	word= 	
NUM= 6352228 TITLE= 너에게 목소리를 보낼게  달빛천사 성우 이용신의 첫 번째 에세이 :doc2vec= [ 0.00986999  0.25820392  0.05965761  0.00871719  0.05071434 -0.19129036
 -0.01507602  0.1607362  -0.14838956  0.02042556 -0.11625506 -0.13551345
 -0.19049414  0.09456768 -0.00624936 -0.03360934  0.08419938 -0.00391634
  0.04873556 -0.19811535 -0.01982189  0.18150046 -0.05749127 -0.06051173
 -0.075945    0.15692773 -0.07358197 -0.1279243  -0.06986962  0.10912792
  0.09279244 -0.06491563 -0.00850757  0.04093218 -0.02052443  

In [239]:
#행의 수를 row_num에 저장
row_num = len(book_data)
row_num

2002

In [240]:
# 1. doc2vec 값을 문자열로 변환
doc2vec_str = doc2vec.tostring()
doc2vec_str

/tmp/ipykernel_18656/669584216.py:2: DeprecationWarning: tostring() is deprecated. Use tobytes() instead.
  doc2vec_str = doc2vec.tostring()


b'\x15\xde\xec;2n\x88>\xcd`}=\xfcH\x10<r1J=WlM\xbe\xd7d\x8f\xbcX\xbc)>f:\x1f\xbe\xe6`\xdc<\xa6\x15\xf6\xbd\xc7)\x10\xbe\xa8SK\xbet\x84\xcb=\xbd\xef\x0e\xbccV\x0c\xbd6\xc2\xb0=\x98\x12d\xbb\xb8\x95W=\xd0HR\xbe\x0c\x9f\xa2\xbc%\xb6B>n{g\xbdP\xfe\x85\xbd\xa4\x17\xa5\xbd\x10<\'>\xca\x8a\xa5\xbd/o\x08\xbeP\xea\x93\xbd\xa41\xe6=\x9dB\xcb=\x03\xea\x88\xbd\xa6\xf4\x07\xbc[\x90@=\x19\xbd\xad\xbc\x7f\xcc8>\xa82\xd8\xbd\xb9\x15?=`s\xb2\xbd\x19{\x04\xbe\x9a\xd7\x0b\xbd\xc2g\x96\xbc\x90t\x8a=\x88A8<pb&>7\xc3\x17\xbeR?\x10<\xfe\x16\x11\xbek~\xf7<"@(\xbd\xce\xd1)=\xcd\xf0\x0b\xbe\xd0J\x92\xbd\xe0\x91E\xbd\x90\xce\x92\xbd\x12\xa4\x11=\x1aN\x88=#\xd0\x9d\xbd\xe9\xd5\x88\xbdw<u\xbd1\x97\x11=35\x03>\xf0N\xff\xbdn\x1b:="\xa5\x03<o\x1aA=@8\xaa<W\xe3\xa7<r\xaeb\xbe\xb2`\xea=F\xf0\x92\xbd\x10W\xdf=D\xb3\xdf=\\\xedK<\xb4\x8d\xa5;*\xad\x9a>\xdfy\xc0\xbd\xb1\xd8\r<\xa8\xeb\x9f\xbd\x81#\xcc<\\\xba\x82\xbdQ\xca\xbc\xbdn\xb5\x15\xbe\x08\xac;>\xc5wK=)\xb0\xef=8\x86!=\xcd\x80P>T:\xe9=,z\xb0;\x12{B=\x88\x97\xe5<3\x1b

In [241]:
# 2. 데이터프레임에 추가
book_data['doc2vec_str'] = doc2vec_str

In [242]:
book_data

SEQ_NO  ISBN_THIRTEEN_NO VLM_NM                              TITLE_NM  \
0     6352228     9791156759270    NaN   너에게 목소리를 보낼게  달빛천사 성우 이용신의 첫 번째 에세이   
1     6352229     9791168120877    NaN  일기에도 거짓말을 쓰는 사람  99년생 시인의 자의식 과잉 에세이   
2     6352230     9791168120839    NaN            본격 한중일 세계사 12  임오군란과 통킹 위기   
3     6352231     9791168120846    NaN   즉시 기분을 바꿔드립니다  신기하게 마음이 편해지는 응급 처방전   
4     6352232     9791168120747    NaN               오늘도 리추얼  음악 나에게 선물하는 시간   
...       ...               ...    ...                                   ...   
1997  6354246     9791164670871    NaN                          학교 서클대화가 필요해   
1998  6354247     9788994229003    NaN                      People Make City   
1999  6354248     9788994027203    NaN                                 동방해경표   
2000  6354249     9791156759126    NaN                      큰글자도서 그렇다면 정상입니다   
2001  6354250     9788988963258    NaN                                 그 사람들   

                  AUTHR_NM PUBLISHER_NM PBLICTE_DE  ADTION_SMBL_NM  PRC_VALUE  \
0                  이용신 지은이          푸른숲        NaN             NaN   160000.0   
1                  차도하 지은이       위즈덤하우스        NaN             NaN   158000.0   
2                굽시니스트 지은이       위즈덤하우스        NaN             NaN   148000.0   
3     올리비아 레메스 지은이 김잔디 옮긴이       위즈덤하우스        NaN             NaN   140000.0   
4                  정혜윤 지은이       위즈덤하우스        NaN             NaN   150000.0   
...                    ...          ...        ...             ...        ...   
1997       손연일 심선화 장경아 지은이          북트리        NaN             NaN   160000.0   
1998               이상환 지은이       디자인로커스        NaN             NaN   150000.0   
1999                 김려 지음        미디어버스        NaN             NaN        NaN   
2000               하지현 지은이          푸른숲        NaN             NaN   360000.0   
2001                김규태 지음           말쌈        NaN             NaN        NaN   

                                              IMAGE_URL  ... KDC_NM  \
0     httpsimagealadincokrproduct284158coverk6528351...  ...    NaN   
1     httpsimagealadincokrproduct2841466coverk202835...  ...    NaN   
2     httpsimagealadincokrproduct2841447coverk402835...  ...    NaN   
3     httpsimagealadincokrproduct2841430coverk892835...  ...    NaN   
4     httpsimagealadincokrproduct2841380coverk202835...  ...    NaN   
...                                                 ...  ...    ...   
1997  httpsimagealadincokrproduct2837599coverk262835...  ...    NaN   
1998  httpsimagealadincokrproduct141865cover89942290...  ...    NaN   
1999                                                NaN  ...    NaN   
2000  httpsimagealadincokrproduct2834689coverk292835...  ...    NaN   
2001                                                NaN  ...    NaN   

       TITLE_SBST_NM AUTHR_SBST_NM TWO_PBLICTE_DE  INTNT_BOOKST_BOOK_EXST_AT  \
0                NaN           NaN     20211203.0                        NaN   
1                NaN           NaN     20211206.0                        NaN   
2                NaN           NaN     20211201.0                        NaN   
3                NaN           NaN     20211201.0                        NaN   
4                NaN           NaN     20211201.0                        NaN   
...              ...           ...            ...                        ...   
1997      학교서클대화가필요해  손연일심선화장경아지은이     20211125.0                          Y   
1998  peoplemakecity        이상환지은이     20111121.0                          Y   
1999           동방해경표          김려지음            NaN                          Y   
2000  큰글자도서그렇다면정상입니다        하지현지은이     20211028.0                          Y   
2001            그사람들         김규태지음            NaN                          Y   

     PORTAL_SITE_BOOK_EXST_AT ISBN_NO  \
0                         NaN     NaN   
1                         NaN     NaN   
2                         NaN     NaN   
3                         NaN     NaN   
4                         NaN     NaN   
...          

In [243]:
book_data.to_csv('../book_data_vector.csv', index=False, encoding='utf-8')

In [244]:
# vector_data = pd.read_csv('../book_data_vector.csv', encoding='utf-8')# 데이터 파일 경로
# vector_data

SEQ_NO  ISBN_THIRTEEN_NO VLM_NM                              TITLE_NM  \
0     6352228     9791156759270    NaN   너에게 목소리를 보낼게  달빛천사 성우 이용신의 첫 번째 에세이   
1     6352229     9791168120877    NaN  일기에도 거짓말을 쓰는 사람  99년생 시인의 자의식 과잉 에세이   
2     6352230     9791168120839    NaN            본격 한중일 세계사 12  임오군란과 통킹 위기   
3     6352231     9791168120846    NaN   즉시 기분을 바꿔드립니다  신기하게 마음이 편해지는 응급 처방전   
4     6352232     9791168120747    NaN               오늘도 리추얼  음악 나에게 선물하는 시간   
...       ...               ...    ...                                   ...   
1997  6354246     9791164670871    NaN                          학교 서클대화가 필요해   
1998  6354247     9788994229003    NaN                      People Make City   
1999  6354248     9788994027203    NaN                                 동방해경표   
2000  6354249     9791156759126    NaN                      큰글자도서 그렇다면 정상입니다   
2001  6354250     9788988963258    NaN                                 그 사람들   

                  AUTHR_NM PUBLISHER_NM PBLICTE_DE  ADTION_SMBL_NM  PRC_VALUE  \
0                  이용신 지은이          푸른숲        NaN             NaN   160000.0   
1                  차도하 지은이       위즈덤하우스        NaN             NaN   158000.0   
2                굽시니스트 지은이       위즈덤하우스        NaN             NaN   148000.0   
3     올리비아 레메스 지은이 김잔디 옮긴이       위즈덤하우스        NaN             NaN   140000.0   
4                  정혜윤 지은이       위즈덤하우스        NaN             NaN   150000.0   
...                    ...          ...        ...             ...        ...   
1997       손연일 심선화 장경아 지은이          북트리        NaN             NaN   160000.0   
1998               이상환 지은이       디자인로커스        NaN             NaN   150000.0   
1999                 김려 지음        미디어버스        NaN             NaN        NaN   
2000               하지현 지은이          푸른숲        NaN             NaN   360000.0   
2001                김규태 지음           말쌈        NaN             NaN        NaN   

                                              IMAGE_URL  ... KDC_NM  \
0     httpsimagealadincokrproduct284158coverk6528351...  ...    NaN   
1     httpsimagealadincokrproduct2841466coverk202835...  ...    NaN   
2     httpsimagealadincokrproduct2841447coverk402835...  ...    NaN   
3     httpsimagealadincokrproduct2841430coverk892835...  ...    NaN   
4     httpsimagealadincokrproduct2841380coverk202835...  ...    NaN   
...                                                 ...  ...    ...   
1997  httpsimagealadincokrproduct2837599coverk262835...  ...    NaN   
1998  httpsimagealadincokrproduct141865cover89942290...  ...    NaN   
1999                                                NaN  ...    NaN   
2000  httpsimagealadincokrproduct2834689coverk292835...  ...    NaN   
2001                                                NaN  ...    NaN   

       TITLE_SBST_NM AUTHR_SBST_NM TWO_PBLICTE_DE  INTNT_BOOKST_BOOK_EXST_AT  \
0                NaN           NaN     20211203.0                        NaN   
1                NaN           NaN     20211206.0                        NaN   
2                NaN           NaN     20211201.0                        NaN   
3                NaN           NaN     20211201.0                        NaN   
4                NaN           NaN     20211201.0                        NaN   
...              ...           ...            ...                        ...   
1997      학교서클대화가필요해  손연일심선화장경아지은이     20211125.0                          Y   
1998  peoplemakecity        이상환지은이     20111121.0                          Y   
1999           동방해경표          김려지음            NaN                          Y   
2000  큰글자도서그렇다면정상입니다        하지현지은이     20211028.0                          Y   
2001            그사람들         김규태지음            NaN                          Y   

     PORTAL_SITE_BOOK_EXST_AT ISBN_NO  \
0                         NaN     NaN   
1                         NaN     NaN   
2                         NaN     NaN   
3                         NaN     NaN   
4                         NaN     NaN   
...          

In [245]:
# string_array = vector_data.loc[0,"doc2vec_str"]
# string_array

'b\'\\x15\\xde\\xec;2n\\x88>\\xcd`}=\\xfcH\\x10<r1J=WlM\\xbe\\xd7d\\x8f\\xbcX\\xbc)>f:\\x1f\\xbe\\xe6`\\xdc<\\xa6\\x15\\xf6\\xbd\\xc7)\\x10\\xbe\\xa8SK\\xbet\\x84\\xcb=\\xbd\\xef\\x0e\\xbccV\\x0c\\xbd6\\xc2\\xb0=\\x98\\x12d\\xbb\\xb8\\x95W=\\xd0HR\\xbe\\x0c\\x9f\\xa2\\xbc%\\xb6B>n{g\\xbdP\\xfe\\x85\\xbd\\xa4\\x17\\xa5\\xbd\\x10<\\\'>\\xca\\x8a\\xa5\\xbd/o\\x08\\xbeP\\xea\\x93\\xbd\\xa41\\xe6=\\x9dB\\xcb=\\x03\\xea\\x88\\xbd\\xa6\\xf4\\x07\\xbc[\\x90@=\\x19\\xbd\\xad\\xbc\\x7f\\xcc8>\\xa82\\xd8\\xbd\\xb9\\x15?=`s\\xb2\\xbd\\x19{\\x04\\xbe\\x9a\\xd7\\x0b\\xbd\\xc2g\\x96\\xbc\\x90t\\x8a=\\x88A8<pb&>7\\xc3\\x17\\xbeR?\\x10<\\xfe\\x16\\x11\\xbek~\\xf7<"@(\\xbd\\xce\\xd1)=\\xcd\\xf0\\x0b\\xbe\\xd0J\\x92\\xbd\\xe0\\x91E\\xbd\\x90\\xce\\x92\\xbd\\x12\\xa4\\x11=\\x1aN\\x88=#\\xd0\\x9d\\xbd\\xe9\\xd5\\x88\\xbdw<u\\xbd1\\x97\\x11=35\\x03>\\xf0N\\xff\\xbdn\\x1b:="\\xa5\\x03<o\\x1aA=@8\\xaa<W\\xe3\\xa7<r\\xaeb\\xbe\\xb2`\\xea=F\\xf0\\x92\\xbd\\x10W\\xdf=D\\xb3\\xdf=\\\\\\xedK<\\xb4\\x8d\\xa5;*\\xad

In [246]:
# # 문자열의 길이를 확인합니다.
# length = len(string_array)

In [247]:
# # 길이가 4 바이트의 배수인지 확인합니다.
# if length % 4 == 0:
#     print("길이는 4 바이트의 배수입니다.")
# else:
#     print("길이는 4 바이트의 배수가 아닙니다.")

길이는 4 바이트의 배수가 아닙니다.


In [248]:
# # 길이가 4 바이트의 배수가 아닌 경우, 패딩을 추가하여 조정합니다.
# if length % 4 != 0:
#     # 패딩을 추가할 필요한 바이트 수를 계산합니다.
#     padding_size = 4 - (length % 4)
    
#     # 널 바이트('\x00')로 패딩을 추가합니다.
#     string_array += '\x00' * padding_size

In [249]:
# # 이제 문자열의 길이는 4 바이트의 배수입니다.
# # 이 문자열을 "float32" 데이터 유형의 NumPy 배열로 변환할 수 있습니다.
# numpy_array = np.fromstring(string_array, dtype="float32")

/tmp/ipykernel_18656/1501493864.py:3: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead
  numpy_array = np.fromstring(string_array, dtype="float32")


In [250]:
# numpy_array

array([1.78610014e+34, 1.78653775e+34, 1.78806524e+34, 1.09074323e-08,
       5.92138895e-05, 1.78682384e+34, 1.86417693e+37, 2.93212096e+23,
       1.78714607e+34, 3.72745227e+30, 2.08126347e+14, 1.78730564e+34,
       1.78806499e+34, 2.56948789e+17, 2.59205331e+17, 1.00004824e+15,
       4.17763697e+21, 8.78306630e-04, 2.09519777e+23, 6.68421915e+22,
       3.41937175e-06, 1.83257954e+22, 1.78676578e+34, 1.78657538e+34,
       1.78653775e+34, 1.78657600e+34, 1.78803330e+34, 1.90520678e+17,
       1.98375949e+17, 2.58264149e+17, 7.91909237e+11, 1.14536073e+21,
       1.78854074e+34, 1.78650692e+34, 2.13227792e+17, 2.57138249e+17,
       2.59403243e+17, 2.58044246e+17, 4.19450633e+21, 9.03530917e-10,
       1.14536242e+21, 1.78657575e+34, 1.78644886e+34, 2.13007872e+17,
       2.07418333e+17, 1.31483402e+22, 1.04440924e+21, 5.39946923e-05,
       6.90930165e-07, 1.78679598e+34, 2.14951330e+11, 6.68421915e+22,
       3.25529976e+21, 2.18964509e+23, 1.31240903e-08, 4.17763697e+21,
      

In [251]:
# # 모든행의 doc2vec_str 컬럼을 출력
# vector_data.loc[: , "doc2vec_str"]

0       b'\x15\xde\xec;2n\x88>\xcd`}=\xfcH\x10<r1J=WlM...
1       b'\x15\xde\xec;2n\x88>\xcd`}=\xfcH\x10<r1J=WlM...
2       b'\x15\xde\xec;2n\x88>\xcd`}=\xfcH\x10<r1J=WlM...
3       b'\x15\xde\xec;2n\x88>\xcd`}=\xfcH\x10<r1J=WlM...
4       b'\x15\xde\xec;2n\x88>\xcd`}=\xfcH\x10<r1J=WlM...
                              ...                        
1997    b'\x15\xde\xec;2n\x88>\xcd`}=\xfcH\x10<r1J=WlM...
1998    b'\x15\xde\xec;2n\x88>\xcd`}=\xfcH\x10<r1J=WlM...
1999    b'\x15\xde\xec;2n\x88>\xcd`}=\xfcH\x10<r1J=WlM...
2000    b'\x15\xde\xec;2n\x88>\xcd`}=\xfcH\x10<r1J=WlM...
2001    b'\x15\xde\xec;2n\x88>\xcd`}=\xfcH\x10<r1J=WlM...
Name: doc2vec_str, Length: 2002, dtype: object

In [252]:
# # 모든행의 synopsys_vector 컬럼을 numpy 배열로 변환 후 데이터 프레임에 저장
# vector_data["doc2vec_numpy"] = vector_data.loc[: , "doc2vec_str"].apply(lambda x: np.fromstring(string_array, dtype="float32"))

/tmp/ipykernel_18656/1815437116.py:2: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead
  vector_data["doc2vec_numpy"] = vector_data.loc[: , "doc2vec_str"].apply(lambda x: np.fromstring(string_array, dtype="float32"))


In [253]:
# vector_data

SEQ_NO  ISBN_THIRTEEN_NO VLM_NM                              TITLE_NM  \
0     6352228     9791156759270    NaN   너에게 목소리를 보낼게  달빛천사 성우 이용신의 첫 번째 에세이   
1     6352229     9791168120877    NaN  일기에도 거짓말을 쓰는 사람  99년생 시인의 자의식 과잉 에세이   
2     6352230     9791168120839    NaN            본격 한중일 세계사 12  임오군란과 통킹 위기   
3     6352231     9791168120846    NaN   즉시 기분을 바꿔드립니다  신기하게 마음이 편해지는 응급 처방전   
4     6352232     9791168120747    NaN               오늘도 리추얼  음악 나에게 선물하는 시간   
...       ...               ...    ...                                   ...   
1997  6354246     9791164670871    NaN                          학교 서클대화가 필요해   
1998  6354247     9788994229003    NaN                      People Make City   
1999  6354248     9788994027203    NaN                                 동방해경표   
2000  6354249     9791156759126    NaN                      큰글자도서 그렇다면 정상입니다   
2001  6354250     9788988963258    NaN                                 그 사람들   

                  AUTHR_NM PUBLISHER_NM PBLICTE_DE  ADTION_SMBL_NM  PRC_VALUE  \
0                  이용신 지은이          푸른숲        NaN             NaN   160000.0   
1                  차도하 지은이       위즈덤하우스        NaN             NaN   158000.0   
2                굽시니스트 지은이       위즈덤하우스        NaN             NaN   148000.0   
3     올리비아 레메스 지은이 김잔디 옮긴이       위즈덤하우스        NaN             NaN   140000.0   
4                  정혜윤 지은이       위즈덤하우스        NaN             NaN   150000.0   
...                    ...          ...        ...             ...        ...   
1997       손연일 심선화 장경아 지은이          북트리        NaN             NaN   160000.0   
1998               이상환 지은이       디자인로커스        NaN             NaN   150000.0   
1999                 김려 지음        미디어버스        NaN             NaN        NaN   
2000               하지현 지은이          푸른숲        NaN             NaN   360000.0   
2001                김규태 지음           말쌈        NaN             NaN        NaN   

                                              IMAGE_URL  ...   TITLE_SBST_NM  \
0     httpsimagealadincokrproduct284158coverk6528351...  ...             NaN   
1     httpsimagealadincokrproduct2841466coverk202835...  ...             NaN   
2     httpsimagealadincokrproduct2841447coverk402835...  ...             NaN   
3     httpsimagealadincokrproduct2841430coverk892835...  ...             NaN   
4     httpsimagealadincokrproduct2841380coverk202835...  ...             NaN   
...                                                 ...  ...             ...   
1997  httpsimagealadincokrproduct2837599coverk262835...  ...      학교서클대화가필요해   
1998  httpsimagealadincokrproduct141865cover89942290...  ...  peoplemakecity   
1999                                                NaN  ...           동방해경표   
2000  httpsimagealadincokrproduct2834689coverk292835...  ...  큰글자도서그렇다면정상입니다   
2001                                                NaN  ...            그사람들   

      AUTHR_SBST_NM TWO_PBLICTE_DE INTNT_BOOKST_BOOK_EXST_AT  \
0               NaN     20211203.0                       NaN   
1               NaN     20211206.0                       NaN   
2               NaN     20211201.0                       NaN   
3               NaN     20211201.0                       NaN   
4               NaN     20211201.0                       NaN   
...             ...            ...                       ...   
1997   손연일심선화장경아지은이     20211125.0                         Y   
1998         이상환지은이     20111121.0                         Y   
1999           김려지음            NaN                         Y   
2000         하지현지은이     20211028.0                         Y   
2001          김규태지음            NaN                         Y   

      PORTAL_SITE_BOOK_EXST_AT ISBN_NO  \
0                          NaN     NaN   
1                          NaN     NaN   
2                          NaN     NaN   
3                          NaN     NaN   
4                          NaN     NaN   
...                        ...     ...   
1997                         Y     NaN   
1998   

In [255]:
# vector_data["doc2vec_numpy"]

0       [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ...
1       [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ...
2       [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ...
3       [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ...
4       [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ...
                              ...                        
1997    [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ...
1998    [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ...
1999    [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ...
2000    [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ...
2001    [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ...
Name: doc2vec_numpy, Length: 2002, dtype: object

In [256]:
# # doc2vec_numpy 배열의 값을 리스트로 변환
# vector_data["doc2vec_numpy"].tolist() # doc2vec_numpy컬럼이 list로 변환 됨

[array([1.78610014e+34, 1.78653775e+34, 1.78806524e+34, 1.09074323e-08,
        5.92138895e-05, 1.78682384e+34, 1.86417693e+37, 2.93212096e+23,
        1.78714607e+34, 3.72745227e+30, 2.08126347e+14, 1.78730564e+34,
        1.78806499e+34, 2.56948789e+17, 2.59205331e+17, 1.00004824e+15,
        4.17763697e+21, 8.78306630e-04, 2.09519777e+23, 6.68421915e+22,
        3.41937175e-06, 1.83257954e+22, 1.78676578e+34, 1.78657538e+34,
        1.78653775e+34, 1.78657600e+34, 1.78803330e+34, 1.90520678e+17,
        1.98375949e+17, 2.58264149e+17, 7.91909237e+11, 1.14536073e+21,
        1.78854074e+34, 1.78650692e+34, 2.13227792e+17, 2.57138249e+17,
        2.59403243e+17, 2.58044246e+17, 4.19450633e+21, 9.03530917e-10,
        1.14536242e+21, 1.78657575e+34, 1.78644886e+34, 2.13007872e+17,
        2.07418333e+17, 1.31483402e+22, 1.04440924e+21, 5.39946923e-05,
        6.90930165e-07, 1.78679598e+34, 2.14951330e+11, 6.68421915e+22,
        3.25529976e+21, 2.18964509e+23, 1.31240903e-08, 4.177636

In [257]:
# # doc2vec_numpy 배열의 값을 리스트로 변환한 값을 numpy 배열로 변환
# np.array(vector_data["doc2vec_numpy"].tolist()) # synopsys_vector_numpy 컬럼 이 이차원 numpy 배열로 변환됨

array([[1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ..., 1.5032952e+07,
        5.4741127e+22, 3.6035973e-39],
       [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ..., 1.5032952e+07,
        5.4741127e+22, 3.6035973e-39],
       [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ..., 1.5032952e+07,
        5.4741127e+22, 3.6035973e-39],
       ...,
       [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ..., 1.5032952e+07,
        5.4741127e+22, 3.6035973e-39],
       [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ..., 1.5032952e+07,
        5.4741127e+22, 3.6035973e-39],
       [1.7861001e+34, 1.7865377e+34, 1.7880652e+34, ..., 1.5032952e+07,
        5.4741127e+22, 3.6035973e-39]], dtype=float32)

StandardScaler()

In [258]:
# from sklearn.discriminant_analysis import StandardScaler

In [ ]:
# # 데이터의 각 열의 평균을 뺀 다음 표준편차로 나워서 평균을 0로 표쥰편차를 1로 변환하는 StandardScaler 객체 생성
# scaler = StandardScaler()

In [254]:
# vector_data.to_csv('../book_data_vector_numpy.csv', index=False, encoding='utf-8')